In [6]:
import json
import pandas as pd

In [7]:
# import numpy as np
from ydata_profiling import ProfileReport

### Compare synthetic and real datasets

In [9]:
train_df = pd.read_csv("../data/tabular/census.csv")
train_report = ProfileReport(train_df, title="Real", minimal=False)

test_df = pd.read_csv("../azure_pilot_outputs/tab_census_ctgan_e300_05/tabular/ctgan/census/census_ctgan_synthetic_data.csv")
test_report = ProfileReport(test_df, title="Synthetic", minimal=False)

In [12]:
comparison_report = train_report.compare(test_report)

In [17]:
# As a JSON string
# json_data = comparison_report.to_json()

# As a file
# comparison_report.to_file("your_report.json")

In [18]:
comparison_report.to_notebook_iframe()

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [7]:
# other formats to export the report
# As a JSON string
# json_data = profile.to_json()

# # As a file
# profile.to_file("your_report.json")
# profile.to_file("your_report.html")

# # As an iframe
# profile.to_notebook_iframe()

### Compare tabular datasets 

In [5]:
from sdv.datasets.demo import get_available_demos
datasets_df = get_available_demos(modality='single_table')
single_table_dataset_names = list(datasets_df["dataset_name"])

In [6]:
cmp_datasets = {
    "name": [],
    "memory_size": [],
    "record_size": [],
    "p_duplicates": [],
    "p_cells_missing": [],
    "n_rows": [],
    "n_cols": [],
    "n_numeric": [],
    "n_categoric": [],
    "n_boolean": [], 
    "n_datetime": [], 
    "n_text": []
}

for dn in single_table_dataset_names:
    try:
        # Load the JSON file into a dictionary
        with open(f"dataset_profiles/{dn}/{dn}.json", "r") as json_file:
            data_dict = json.load(json_file)
        
        tab_data = data_dict["table"]
        cmp_datasets["name"].append(dn)
        cmp_datasets["memory_size"].append(tab_data["memory_size"])
        cmp_datasets["record_size"].append(tab_data["record_size"])
        cmp_datasets["p_duplicates"].append(tab_data["p_duplicates"])
        cmp_datasets["p_cells_missing"].append(tab_data["p_cells_missing"])
        cmp_datasets["n_rows"].append(tab_data["n"])
        cmp_datasets["n_cols"].append(tab_data["n_var"])
        cmp_datasets["n_numeric"].append(tab_data["types"]["Numeric"])
        try:
            cmp_datasets["n_categoric"].append(tab_data["types"]["Categorical"])
        except Exception as e:
            cmp_datasets["n_categoric"].append(0)
        try:
            cmp_datasets["n_boolean"].append(tab_data["types"]["Boolean"])
        except Exception as e:
            cmp_datasets["n_boolean"].append(0)
            
        try:
            cmp_datasets["n_text"].append(tab_data["types"]["Text"])
        except Exception as e:
            cmp_datasets["n_text"].append(0)
            
        try:
            cmp_datasets["n_datetime"].append(tab_data["types"]["DateTime"])
        except Exception as e:
            cmp_datasets["n_datetime"].append(0)
             
    except Exception as e: 
        print(e)

[Errno 2] No such file or directory: 'dataset_profiles/KRK_v1/KRK_v1.json'
[Errno 2] No such file or directory: 'dataset_profiles/adult/adult.json'
[Errno 2] No such file or directory: 'dataset_profiles/alarm/alarm.json'
[Errno 2] No such file or directory: 'dataset_profiles/asia/asia.json'
[Errno 2] No such file or directory: 'dataset_profiles/census/census.json'
[Errno 2] No such file or directory: 'dataset_profiles/census_extended/census_extended.json'
[Errno 2] No such file or directory: 'dataset_profiles/child/child.json'
[Errno 2] No such file or directory: 'dataset_profiles/covtype/covtype.json'
[Errno 2] No such file or directory: 'dataset_profiles/credit/credit.json'
[Errno 2] No such file or directory: 'dataset_profiles/expedia_hotel_logs/expedia_hotel_logs.json'
[Errno 2] No such file or directory: 'dataset_profiles/fake_companies/fake_companies.json'
[Errno 2] No such file or directory: 'dataset_profiles/fake_hotel_guests/fake_hotel_guests.json'
[Errno 2] No such file or di

In [10]:
cmp_datasets_df = pd.DataFrame(cmp_datasets)

In [11]:
cmp_datasets_df

Empty DataFrame
Columns: [name, memory_size, record_size, p_duplicates, p_cells_missing, n_rows, n_cols, n_numeric, n_categoric, n_boolean, n_datetime, n_text]
Index: []

In [9]:
data_list = ["adult", "census", "alarm", "child", "covtype", "credit", "expedia_hotel_logs", "insurance", "intrusion"]
filtered_df = cmp_datasets_df[cmp_datasets_df["name"].isin(data_list)]

In [ ]:
filtered_df

In [19]:
import pandas as pd
import numpy as np
from sklearn.metrics.pairwise import euclidean_distances

def distance_to_closest_records(synthetic_data, real_data):
    distances = euclidean_distances(synthetic_data, real_data)
    min_distances = np.min(distances, axis=1)
    return min_distances

# Example usage
synthetic_data = pd.DataFrame({
    'Feature1': [0.5, 0.2, 0.9],
    'Feature2': [0.8, 0.4, 0.1]
})

real_data = pd.DataFrame({
    'Feature1': [0.6, 0.3, 0.8],
    'Feature2': [0.7, 0.5, 0.2]
})

# Convert categorical features to numeric using one-hot encoding
synthetic_data = pd.get_dummies(synthetic_data)
real_data = pd.get_dummies(real_data)

synthetic_array = synthetic_data.to_numpy()
real_array = real_data.to_numpy()

distances = distance_to_closest_records(synthetic_array, real_array)
print("Distance to closest real records:", distances)

Distance to closest real records: [0.14142136 0.14142136 0.14142136]


In [25]:
import numpy as np
from scipy.stats import iqr

def outlier_coverage_score(real_data, synthetic_data):
    # Calculate IQR for real data
    q1_real = real_data.quantile(0.25)
    q3_real = real_data.quantile(0.75)
    iqr_real = q3_real - q1_real
    
    # Define outlier ranges for real data
    lower_bound_real = q1_real - 1.5 * iqr_real
    upper_bound_real = q3_real + 1.5 * iqr_real
    
    # Count outliers in real data
    real_outliers = real_data[(real_data < lower_bound_real) | (real_data > upper_bound_real)]
    num_real_outliers = len(real_outliers)
    
    # Calculate IQR for synthetic data
    q1_synthetic = synthetic_data.quantile(0.25)
    q3_synthetic = synthetic_data.quantile(0.75)
    iqr_synthetic = q3_synthetic - q1_synthetic
    
    # Define outlier ranges for synthetic data
    lower_bound_synthetic = q1_synthetic - 1.5 * iqr_synthetic
    upper_bound_synthetic = q3_synthetic + 1.5 * iqr_synthetic
    
    # Count outliers in synthetic data within the real outlier ranges
    synthetic_outliers = synthetic_data[(synthetic_data >= lower_bound_real) & (synthetic_data <= upper_bound_real)]
    num_synthetic_outliers = len(synthetic_outliers)
    
    # Calculate the coverage score
    coverage_score = num_synthetic_outliers / num_real_outliers if num_real_outliers > 0 else 0.0
    return coverage_score

# Example usage
real_data = pd.Series([10, 15, 20, 25, 30, 200])  # Example real data with an outlier (200)
synthetic_data = pd.Series([12, 14, 18, 22, 27, 28])  # Example synthetic data

score = outlier_coverage_score(real_data, synthetic_data)
print("Outlier Coverage Score:", score)


Outlier Coverage Score: 6.0


In [33]:
import numpy as np
from scipy.stats import iqr

def outlier_coverage_score(real_data, synthetic_data):
    # Calculate IQR for real data
    q1_real, q3_real = real_data.quantile([0.25, 0.75])
    iqr_real = q3_real - q1_real
    
    # Define outlier ranges for real data
    lower_bound_real = q1_real - 1.5 * iqr_real
    upper_bound_real = q3_real + 1.5 * iqr_real
    
    # Count outliers in real data
    real_outliers = real_data[(real_data < lower_bound_real) | (real_data > upper_bound_real)]
    num_real_outliers = len(real_outliers)
    total_real_points = len(real_data)
    
    # Calculate IQR for synthetic data
    q1_synthetic, q3_synthetic = synthetic_data.quantile([0.25, 0.75])
    iqr_synthetic = q3_synthetic - q1_synthetic
    
    # Define outlier ranges for synthetic data
    lower_bound_synthetic = q1_synthetic - 1.5 * iqr_synthetic
    upper_bound_synthetic = q3_synthetic + 1.5 * iqr_synthetic
    
    # Count outliers in synthetic data within the real outlier ranges
    synthetic_outliers = synthetic_data[(synthetic_data >= lower_bound_real) & (synthetic_data <= upper_bound_real)]
    num_synthetic_outliers = len(synthetic_outliers)
    total_synthetic_points = len(synthetic_data)
    
    # Calculate the coverage score
    p_real = num_real_outliers / total_real_points
    p_synthetic = num_synthetic_outliers / total_synthetic_points
    score = min(p_synthetic / p_real, 1)
    
    return score

# Example usage
real_data = pd.Series([10, 15, 20, 5, 30, 200])  # Example real data with an outlier (200)
synthetic_data = pd.Series([12, 14, 10, 22, 20, 28])  # Example synthetic data

score = outlier_coverage_score(real_data, synthetic_data)
print("Normalized Outlier Coverage Score:", score)


Normalized Outlier Coverage Score: 1


In [67]:
import numpy as np
from scipy.stats import iqr

def calculate_num_outliers(data):
    q1, q3 = data.quantile([0.25, 0.75])
    iqr_value = q3 - q1
    
    print(q1, q3)
    
    lower_bound = q1 - 1.5 * iqr_value
    upper_bound = q3 + 1.5 * iqr_value
    
    print(lower_bound, upper_bound)
    
    outliers = data[(data < lower_bound) | (data > upper_bound)]
    # print("outliers ", q1, q3 , iqr_value, lower_bound, upper_bound)
    num_outliers = len(outliers)
    total_points = len(data)
    return num_outliers, total_points

def outlier_coverage_score(real_data, synthetic_data):
    num_real_outliers, total_real_points = calculate_num_outliers(real_data)
    num_synthetic_outliers, total_synthetic_points = calculate_num_outliers(synthetic_data)
    
    p_real = num_real_outliers / total_real_points
    p_synthetic = num_synthetic_outliers / total_synthetic_points
    score = min(p_synthetic / p_real, 1)
    
    return score

# Example usage
real_data = pd.Series([10, 15, 20, 25, -0.0009999999009999, 30, 200])  # Example real data with an outlier (200)
synthetic_data = pd.Series([12, 14, 18, 22, -0.9999, 27, 200])  # Example synthetic data

score = outlier_coverage_score(real_data, synthetic_data)
print("Normalized Outlier Coverage Score:", score)


12.5 27.5
-10.0 50.0
13.0 24.5
-4.25 41.75
Normalized Outlier Coverage Score: 1.0


In [47]:
import pandas as pd

# Example data
data = pd.Series([10, 20, 30, 40, 50, 60, 70, 80, 90, 100])

# Calculate different quantiles
q1 = data.quantile(0.25)  # 25th percentile (Q1)
q2 = data.quantile(0.50)  # 50th percentile (median)
q3 = data.quantile(0.75)  # 75th percentile (Q3)

print("Q1 (25th percentile):", q1)
print("Median (50th percentile):", q2)
print("Q3 (75th percentile):", q3)

Q1 (25th percentile): 32.5
Median (50th percentile): 55.0
Q3 (75th percentile): 77.5


In [48]:
import pandas as pd

# Example data
data = pd.Series([10, 20, 30, 40, 50, 60, 70, 80, 90, 100])

# Calculate and print the 25th percentile (Q1)
q1 = data.quantile(0.25)
print("Q1 (25th percentile):", q1)  

Q1 (25th percentile): 32.5


In [69]:
import numpy as np
from scipy.stats import iqr

def calculate_num_outliers(data):
    """
    Calculate the number of outliers in a dataset and the total number of data points.

    Parameters:
        data (pandas.Series): The input data for which to calculate outliers.

    Returns:
        num_outliers (int): Number of outliers in the dataset.
        total_points (int): Total number of data points in the dataset.
    """
    # Calculate the first and third quartiles
    q1, q3 = data.quantile([0.25, 0.75])
    # Calculate the interquartile range (IQR)
    iqr_value = q3 - q1
    
    # Calculate lower and upper bounds for outliers
    lower_bound = q1 - 1.5 * iqr_value
    upper_bound = q3 + 1.5 * iqr_value
    
    # Identify outliers within the defined bounds
    outliers = data[(data < lower_bound) | (data > upper_bound)]
    
    # Calculate the number of outliers and total data points
    num_outliers = len(outliers)
    total_points = len(data)
    
    return num_outliers, total_points

def outlier_coverage_score(real_data, synthetic_data):
    """
    Calculate the outlier coverage score between real and synthetic datasets.

    Parameters:
        real_data (pandas.Series): The real dataset containing outliers.
        synthetic_data (pandas.Series): The synthetic dataset to be evaluated.

    Returns:
        score (float): The outlier coverage score.
    """
    # Calculate the number of outliers and total data points for real data
    num_real_outliers, total_real_points = calculate_num_outliers(real_data)
    # Calculate the number of outliers and total data points for synthetic data
    num_synthetic_outliers, total_synthetic_points = calculate_num_outliers(synthetic_data)
    
    # Calculate the proportions of outliers
    p_real = num_real_outliers / total_real_points
    p_synthetic = num_synthetic_outliers / total_synthetic_points
    
    # Calculate the outlier coverage score
    score = min(p_synthetic / p_real, 1)
    
    return score

# Example usage
real_data = pd.Series([10, 15, 20, 25, -0.0009999999009999, 30, 200])  # Example real data with an outlier (200)
synthetic_data = pd.Series([12, 14, 18, 22, -0.9999, 27, 200])  # Example synthetic data

score = outlier_coverage_score(real_data, synthetic_data)
print("Normalized Outlier Coverage Score:", score)

Normalized Outlier Coverage Score: 1.0


In [119]:
import numpy as np
from scipy.stats import wasserstein_distance, entropy
from scipy.spatial.distance import jensenshannon
from sklearn.preprocessing import MinMaxScaler

def compute_distance(data1, data2):
    """
    Compute the appropriate distance (Wasserstein or Jensen-Shannon) based on data type.

    Parameters:
        data1 (pandas.Series): The first dataset.
        data2 (pandas.Series): The second dataset.

    Returns:
        distance (float): The calculated distance.
    """
    if data1.dtype == "object":
        # Categorical data: Use Jensen-Shannon distance
        categories = data1.unique()
        real_counts = data1.value_counts()
        fake_counts = data2.value_counts()

        real_pdf = real_counts / len(data1)
        fake_pdf = fake_counts / len(data2)

        categories = real_pdf.index.tolist()
        real_pdf_values = real_pdf.values.tolist()
        fake_pdf_values = [fake_pdf.get(cat, 0) for cat in categories]
        
        print(real_pdf_values)
        print(type(fake_pdf_values), fake_pdf_values)

        js_distance = jensenshannon(real_pdf_values, fake_pdf_values, 2.0)
        return js_distance
    else:
        # Numerical data: Use Wasserstein distance
        scaler = MinMaxScaler()
        real_scaled = scaler.fit_transform(data1.values.reshape(-1, 1)).flatten()
        fake_scaled = scaler.transform(data2.values.reshape(-1, 1)).flatten()

        w_distance = wasserstein_distance(real_scaled, fake_scaled)
        return w_distance

# # Example usage
# real_data = pd.Series([...])  # Replace with your real data
# fake_data = pd.Series([...])  # Replace with your fake data

# distance = compute_distance(real_data, fake_data)
# print("Distance:", distance)


In [121]:
import numpy as np
import pandas as pd
from scipy.stats import wasserstein_distance
from scipy.spatial.distance import jensenshannon
from sklearn.preprocessing import MinMaxScaler

def compute_distance(data1, data2):
    """
    Compute the appropriate distance (Wasserstein or Jensen-Shannon) based on data type.

    Parameters:
        data1 (pandas.Series): The first dataset.
        data2 (pandas.Series): The second dataset.

    Returns:
        distance (float): The calculated distance.
    """
    # Drop missing values
    data1_cleaned = data1.dropna()
    data2_cleaned = data2.dropna()

    if data1_cleaned.dtype == "object":
        # Categorical data: Use Jensen-Shannon distance
        categories = data1_cleaned.unique()
        real_counts = data1_cleaned.value_counts()
        fake_counts = data2_cleaned.value_counts()

        real_pdf = real_counts / len(data1_cleaned)
        fake_pdf = fake_counts / len(data2_cleaned)

        categories = real_pdf.index.tolist()
        real_pdf_values = real_pdf.values.tolist()
        fake_pdf_values = [fake_pdf.get(cat, 0) for cat in categories]

        js_distance = jensenshannon(real_pdf_values, fake_pdf_values, 2.0)
        return js_distance
    else:
        # Numerical data: Use Wasserstein distance
        scaler = MinMaxScaler()
        real_scaled = scaler.fit_transform(data1_cleaned.values.reshape(-1, 1)).flatten()
        fake_scaled = scaler.transform(data2_cleaned.values.reshape(-1, 1)).flatten()

        w_distance = wasserstein_distance(real_scaled, fake_scaled)
        return w_distance

# # Example usage
# categorical_data = pd.Series(["A", "B", "A", np.nan, "B", "C"])
# numerical_data = pd.Series([10, 20, 15, 25, 18, np.nan])

# categorical_distance = compute_distance(categorical_data, categorical_data)
# numerical_distance = compute_distance(numerical_data, numerical_data)

# print("Categorical Distance:", categorical_distance)
# print("Numerical Distance:", numerical_distance)


In [123]:

# Define example data
categorical_data = pd.Series(["m", "D", np.nan, "A", "C", "B", "C"])
categorical_data2 = pd.Series(["A", "A", "A", "B", "B", "C"])
numerical_data = pd.Series([10, 20, 15, 25, np.nan, 18, 30])
numerical_data2 = pd.Series([40, 21, 20, 25, 18, 30])

# Test categorical distance
categorical_distance = compute_distance(categorical_data, categorical_data2)
print("Categorical Distance:", categorical_distance)

# Test numerical distance
numerical_distance = compute_distance(numerical_data, numerical_data2)
print("Numerical Distance:", numerical_distance)




Categorical Distance: 0.5200250392878958
Numerical Distance: 0.3


In [106]:
set(categorical_data.value_counts(
                ).keys())-set(categorical_data2.value_counts().keys())

{'D', 'm'}

In [100]:
categorical_data.value_counts().sum()

A    2
C    2
D    1
B    1
Name: count, dtype: int64

In [101]:
real_pdf = categorical_data.value_counts()/categorical_data.value_counts().sum()

In [102]:
real_pdf

A    0.333333
C    0.333333
D    0.166667
B    0.166667
Name: count, dtype: float64

In [89]:
categories = (categorical_data.value_counts()/categorical_data.value_counts().sum()).keys().tolist()

In [96]:
categories

['C', 'Z', 'D', 'A', 'B']

In [92]:
sorted_categories = sorted(categories)

In [94]:
real_pdf_values = []

for i in sorted_categories:
    real_pdf_values.append(real_pdf[i])


In [95]:
real_pdf_values

[0.16666666666666666,
 0.16666666666666666,
 0.3333333333333333,
 0.16666666666666666,
 0.16666666666666666]

In [ ]:
 zero_cats = set(really[column].value_counts(
                ).keys())-set(fakey[column].value_counts().keys())
                for z in zero_cats:
                    real_pdf_values.append(real_pdf[z])
                    fake_pdf_values.append(0)